In [1]:
import numpy as np #linear algebra 
import pandas as pd #data processing, CSV file I/O
from matplotlib import pyplot as plt #data vis
import seaborn as sns #stat data vis 
import statsmodels.api as sm 
import scipy.stats as stats 
from sklearn.preprocessing import LabelEncoder
import copy 
sns.set() #setting the default seaborn style for our plots

Matplotlib is building the font cache; this may take a moment.


In [2]:
#Read the Dataset 
seed_df = pd.read_csv("Streamlined for Gretel - Line-list.csv")
syn_df = pd.read_csv("synthetic-example.csv")

In [3]:
set(seed_df.columns).intersection(set(syn_df.columns))

{'If_onset_approximated',
 'age',
 'country',
 'death',
 'exposure_end',
 'exposure_start',
 'from Wuhan',
 'gender',
 'hosp_visit_date',
 'id',
 'location',
 'recovered',
 'reporting date',
 'symptom_onset',
 'symptoms recorded',
 'visiting Wuhan'}

In [4]:
syn_df.head

<bound method NDFrame.head of      Unnamed: 0    id reporting date    location country gender  age  \
0             0  3179         3/1/20         NaN     NaN    NaN  NaN   
1             1   551         3/5/20         NaN     NaN    NaN  NaN   
2             2   534         3/4/20         NaN     NaN    NaN  NaN   
3             3   537         3/5/20         NaN     NaN    NaN  NaN   
4             4   514         3/4/20         NaN     NaN    NaN  NaN   
..          ...   ...            ...         ...     ...    ...  ...   
995         995  3203         3/3/20         NaN     NaN    NaN  NaN   
996         996  2253        3/12/20   Louisiana     USA    NaN  NaN   
997         997  2297        3/11/20  Washington     USA    NaN  NaN   
998         998  1998        3/11/20    New York     USA    NaN  NaN   
999         999  1855        3/10/20  Washington     USA    NaN  NaN   

    symptom_onset  If_onset_approximated hosp_visit_date exposure_start  \
0             NaN             

In [5]:
seed_df.head

<bound method NDFrame.head of         id reporting date             location      country  gender   age  \
0        1      1/20/2020  Shenzhen, Guangdong        China    male  66.0   
1        1      1/20/2020             Shanghai        China  female  56.0   
2        2      1/21/2020             Zhejiang        China    male  46.0   
3        3      1/21/2020              Tianjin        China  female  60.0   
4        4      1/21/2020              Tianjin        China    male  58.0   
...    ...            ...                  ...          ...     ...   ...   
3392  3392      2/27/2020               Aargau  Switzerland    male  26.0   
3393  3393      2/27/2020               Zurich  Switzerland  female  30.0   
3394  3394      2/27/2020                 Vaud  Switzerland    male  49.0   
3395  3395      2/27/2020          Basal-Stadt  Switzerland  female   NaN   
3396  3396      2/28/2020          Basal-Stadt  Switzerland    male  23.0   

     symptom_onset  If_onset_approximated hos

In [6]:
syn_df.shape, syn_df.size

((1000, 17), 17000)

In [7]:
seed_df.shape, seed_df.size

((3397, 21), 71337)

In [8]:
set(seed_df.columns) - set(seed_df.columns).intersection(set(syn_df.columns))

{'breathing', 'cough', 'fever', 'malaise', 'throat'}

In [9]:
set(syn_df.columns) - set(seed_df.columns).intersection(set(syn_df.columns))

{'Unnamed: 0'}

In [10]:
pd.__version__, np.__version__

('1.2.3', '1.20.1')

In [11]:
seed_df.describe()

id          age  If_onset_approximated  visiting Wuhan  \
count  3397.000000  1507.000000             655.000000     1606.000000   
mean   1698.000294    51.040312               0.117557        0.120174   
std     980.773250    18.813253               2.077971        0.325267   
min       1.000000     0.250000               0.000000        0.000000   
25%     849.000000    36.000000               0.000000        0.000000   
50%    1698.000000    54.000000               0.000000        0.000000   
75%    2547.000000    65.000000               0.000000        0.000000   
max    3396.000000    96.000000              53.000000        1.000000   

        from Wuhan  symptoms recorded        cough    breathing        fever  \
count  1602.000000        3397.000000  3397.000000  3397.000000  3397.000000   
mean      0.097378           0.099500     0.044451     0.006771     0.082131   
std       0.296565           0.299376     0.206125     0.082017     0.274605   
min       0.000000           0.000000     0.000000     0.000000     0.000000   
25%       0.000000           0.000000     0.000000     0.000000     0.000000   
50%       0.000000           0.000000     0.000000     0.000000     0.000000   
75%       0.000000           0.000000     0.000000     0.000000     0.000000   
max       1.000000           1.000000     1.000000     1.000000     1.000000   

            throat      malaise  
count  3397.000000  3397.000000  
mean      0.019135     0.018546  
std       0.137018     0.134934  
min       0.000000     0.000000  
25%       0.000000     0.000000  
50%       0.000000     0.000000  
75%       0.000000     0.000000  
max       1.000000     1.000000

In [12]:
syn_df.describe()

Unnamed: 0           id         age  If_onset_approximated  \
count  1000.000000  1000.000000  367.000000             135.000000   
mean    499.500000  1821.530000   51.239782               0.007407   
std     288.819436   967.327948   18.059472               0.086066   
min       0.000000     6.000000    5.000000               0.000000   
25%     249.750000  1001.500000   36.500000               0.000000   
50%     499.500000  1807.500000   54.000000               0.000000   
75%     749.250000  2689.250000   65.000000               0.000000   
max     999.000000  3394.000000   96.000000               1.000000   

       visiting Wuhan  from Wuhan  symptoms recorded  
count      463.000000  470.000000        1000.000000  
mean         0.053996    0.025532           0.089000  
std          0.226254    0.157902           0.284886  
min          0.000000    0.000000           0.000000  
25%          0.000000    0.000000           0.000000  
50%          0.000000    0.000000           0.000000  
75%          0.000000    0.000000           0.000000  
max          1.000000    1.000000           1.000000

In [13]:
seed_df.isna().sum()

id                          0
reporting date              1
location                  230
country                   163
gender                   1712
age                      1890
symptom_onset            2713
If_onset_approximated    2742
hosp_visit_date          2777
exposure_start           3203
exposure_end             2909
visiting Wuhan           1791
from Wuhan               1795
death                    1778
recovered                1791
symptoms recorded           0
cough                       0
breathing                   0
fever                       0
throat                      0
malaise                     0
dtype: int64

In [14]:
syn_df.isna().sum()

Unnamed: 0                 0
id                         0
reporting date             0
location                  73
country                   49
gender                   587
age                      633
symptom_onset            856
If_onset_approximated    865
hosp_visit_date          874
exposure_start           975
exposure_end             907
visiting Wuhan           537
from Wuhan               530
death                    529
recovered                530
symptoms recorded          0
dtype: int64

In [15]:
!pip install pandas-profiling

In [16]:
from pandas_profiling import ProfileReport

In [17]:
profile1 = ProfileReport(seed_df, title="Seed dataset Pandas Profiling Report")
profile = ProfileReport(syn_df, title="Synthetic dataset Pandas Profiling Report")

In [18]:
profile.to_notebook_iframe()

Summarize dataset:   0%|          | 0/30 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

In [22]:
profile1.to_notebook_iframe()

In [23]:
profile1.to_file("Seed_report.html")
profile.to_file("Syn_report.html")

Export report to file:   0%|          | 0/1 [00:00<?, ?it/s]

Export report to file:   0%|          | 0/1 [00:00<?, ?it/s]